# 1) Imports

In [1]:
import secrets
import string
import folium
import branca
import pandas as pd 
import numpy as np
import streamlit as st
import plotly.express as px
import plotly.io as pio
import geopandas as gpd
import plotly.graph_objs as go
from millify import millify
from shapely import wkt
from shapely.geometry import shape
from streamlit_folium import folium_static
from geopy.distance import great_circle
from plotly.subplots import make_subplots

# 2) Funções

In [83]:
def carregar_municipios_sertao():
    all_muns = pd.read_csv(r"C:/Users/User/Documents/GitHub/BCG2023/Dados/Tabela_final/municipios_clusters.csv")
    lim_muns = pd.read_json(r'C:/Users/User/Documents/GitHub/BCG2023/Dados/Views/municipios-poligonos.json')
    lim_muns['poligono'] = [str(polygon) for polygon in lim_muns['poligono']]
    lim_muns['geometry'] = lim_muns['poligono'].apply(lambda x: shape(eval(x)))
    lim_muns = lim_muns[['municipioCodigo', 'geometry']].rename(columns={'municipioCodigo':'IBGE7'})
    all_muns = all_muns.merge(lim_muns, on = 'IBGE7', how = 'inner')
    all_muns = gpd.GeoDataFrame(all_muns, geometry='geometry')
    all_muns = all_muns.set_crs("EPSG:4326")
    return all_muns

def carregar_agro():
    agro = pd.read_csv(r"C:/Users/User/Documents/GitHub/BCG2023/Dados/Tabela_final/dados_producao_agricola.csv").drop(columns='Unnamed: 0')
    return agro

def carregar_solos(_all_muns):
    solos = pd.read_csv(r"C:/Users/User/Documents/GitHub/BCG2023/Dados/Views/solos_municipios.csv").drop(columns='Unnamed: 0')
    solos = _all_muns[['IBGE7', 'NOME']].merge(solos, on = 'IBGE7', how = 'inner').drop(columns='IBGE7')
    solos['AREA_TOTAL'] = round(solos['AREA_TOTAL'],2)
    return solos

def muns_prox(mun_df, all_muns, raio):
    coordenadas_mun = (mun_df['LATITUDE'].iloc[0], mun_df['LONGITUDE'].iloc[0])
    muns_prox = {}
    for _, row in all_muns.iterrows():
        coordenadas_muns_prox = (row['LATITUDE'], row['LONGITUDE'])
        distancia = great_circle(coordenadas_mun, coordenadas_muns_prox).kilometers
        if distancia <= raio:
            muns_prox[row['NOME']] = round(distancia,2)
    return muns_prox

def comp_df(metric, mun_df, all_muns, muns_prox_names):
    mun_metric = mun_df[metric].iloc[0]
    muns_prox_df = all_muns[metric].loc[all_muns['NOME'].isin(muns_prox_names)].mean()
    comp_df = pd.DataFrame()
    comp_df.insert(0, 'NOME', ['Município Potencial', 'Média do Entorno'])
    comp_df.insert(1, metric, [round(mun_metric,1), round(muns_prox_df,1)])
    return comp_df

def agro_comp(agro, mun_name, metric, muns_prox_names):
    if metric in ['VALOR_PROD', 'AREA_PLANTADA']:
        agro_mun = agro[['PRODUTO', metric]].loc[agro['NOME']==mun_name]
        agro_mun = agro_mun.groupby('PRODUTO').sum().reset_index()
        agro_mun[metric] = round(agro_mun[metric],2)
        agro_mun = agro_mun.sort_values(by=metric)
        agro_prox = agro[['PRODUTO', metric]].loc[agro['NOME'].isin(muns_prox_names)]
        agro_prox = agro_prox.groupby('PRODUTO').sum().reset_index()
        agro_prox[metric] = round(agro_prox[metric],2)
        agro_prox = agro_prox.sort_values(by=metric)

    elif metric == 'REND_AREA':
        agro['REND_AREA'] = agro['VALOR_PROD']/agro['AREA_PLANTADA']
        agro_mun = agro[['PRODUTO', 'REND_AREA']].loc[agro['NOME']==mun_name]
        agro_mun = agro_mun.groupby('PRODUTO').mean().reset_index()
        agro_mun['REND_AREA'] = round(agro_mun['REND_AREA'],2)
        agro_mun = agro_mun.sort_values(by=metric)
        agro_prox = agro[['PRODUTO', 'REND_AREA']].loc[agro['NOME'].isin(muns_prox_names)]
        agro_prox = agro_prox.groupby('PRODUTO').mean().reset_index()
        agro_prox['REND_AREA'] = round(agro_prox['REND_AREA'],2)
        agro_prox = agro_prox.sort_values(by=metric)
    return agro_mun, agro_prox

def tipos_de_solo(solos, nome_mun):
    solos_prox = solos[solos['NOME']==nome_mun].drop(columns=['NOME'])
    solos_prox = solos_prox.groupby('SOLO').sum().reset_index().sort_values(by='AREA_TOTAL', ascending = False)
    return solos_prox.reset_index().drop(columns='index')

def generate_random_key(length=16):
    characters = string.ascii_letters + string.digits
    random_key = ''.join(secrets.choice(characters) for _ in range(length))
    return random_key

def bar_plot(df, x, y, title, leg_x, leg_y, text):
    df = df.sort_values(by=x)
    fig = px.bar(
        df, 
        x=x, 
        y=y, 
        orientation='h', 
        text = text,
        color='NOME',
        category_orders={'NOME': ['Município Potencial', 'Média do Entorno']}
        )
    fig.data[0].update(showlegend=False)
    fig.data[1].update(showlegend=False)
    fig.update_xaxes(title_text=leg_x)
    fig.update_yaxes(title_text=leg_y)
    fig.update_layout(title=title)
    fig.show()

# 2) Coleta dos dados

In [3]:
all_muns = carregar_municipios_sertao().drop(columns='Unnamed: 0')
agro = carregar_agro()
solos = carregar_solos(all_muns)

# 3) Análise dos dados

## 3.1) Informações geográficas

In [5]:
cluster = 1
mun = 'ITAPICURU'
mun_df = all_muns[(all_muns['NOME']==mun)&(all_muns['CLUSTER']==cluster)]
uf = mun_df['UF'].iloc[0]
capital_prox = mun_df['CAPITAL_PROXIMA'].iloc[0]
pop_tot = millify(mun_df['POP_TOT'], precision=1, drop_nulls=False)
pop_tot_30 = millify(mun_df['POP_TOT_30KM'], precision=1, drop_nulls=False)
dist_capital = millify(mun_df['DIST_CAPITAL'], precision=0, drop_nulls=False)
custo_transporte = millify(mun_df['TRANSPORT_COST'], precision=2, drop_nulls=False)
print('UF:',uf)
print('Capital mais próxima:', capital_prox)
print('População:',pop_tot)
print('População em um raio de 30Km:',pop_tot_30)
print('Distância até a capital mais próxima:',dist_capital)
print('Custo de transporte para o porto mais próximo:',custo_transporte)

UF: BA
Capital mais próxima: ARACAJU
População: 35.9k
População em um raio de 30Km: 197.8k
Distância até a capital mais próxima: 134
Custo de transporte para o porto mais próximo: 23.77k


## 3.2) Dados socioeconômicos

In [6]:
idh = millify(mun_df['IDHM'], precision=3, drop_nulls=False)
renda = millify(float(mun_df['RDPC']), precision=2, drop_nulls=False)
i_freq = round(float(mun_df['I_FREQ_PROP'])*100,2)
t_analf = round(float(mun_df['T_ANALF15M']),2)
desocup = float(mun_df['T_DES18M'])
pind = float(mun_df['PIND'])
print('IDH:', idh)
print('Renda per capita:', f"R$ {renda}")
print('Subíndice de frequência escolar:', f"{i_freq} %")
print('Taxa de analfabetismo (acima de 15 anos):', f"{t_analf} %")
print('Taxa de desocupação (acima de 18 anos):', f"{desocup} %")
print('Percentual de extramemente pobres:', f"{pind} %")

IDH: 0.486
Renda per capita: R$ 185.70
Subíndice de frequência escolar: 46.2 %
Taxa de analfabetismo (acima de 15 anos): 38.52 %
Taxa de desocupação (acima de 18 anos): 9.86 %
Percentual de extramemente pobres: 31.44 %


## 3.3) Análise comparativa do entorno

In [74]:
critério_de_similaridade = 'Proximidade Geográfica'
raio = 50
muns_prox_dict = muns_prox(mun_df, all_muns, raio)
muns_prox_names = [nome for nome in list(muns_prox_dict.keys()) if nome != mun_df['NOME'].iloc[0]]

### 3.3.1) Mapa

In [42]:
tipo_de_metrica = 'Recursos hídricos'
metrica_alias = "Precipitação média anual (mm)"
metrica = 'PREC_MED'

centroids = all_muns[['NOME', 'geometry']].copy()
centroids.crs = 'epsg:32724'

colormap = branca.colormap.LinearColormap(
    vmin=all_muns[metrica].quantile(0.0),
    vmax=all_muns[metrica].quantile(1),
    colors=[
        "red",
        "orange",
        "yellow",
        "green", 
        "blue"
    ],
    caption=metrica_alias)
    
m = folium.Map(
    location=[
        centroids[centroids['NOME']==mun].centroid.values[0].y, 
        centroids[centroids['NOME']==mun].centroid.values[0].x
    ], 
    zoom_start=8.5
)

tooltip = folium.GeoJsonTooltip(
    fields=["IBGE7", "NOME", metrica],
    aliases=["Código do IBGE:", "Nome:", f"{metrica_alias}:"],
    localize=True,
    sticky=False,
    labels=True,
    style="""
        background-color: #F0EFEF;
    """,
    max_width=800,
)

g = folium.GeoJson(
    all_muns,
    style_function=lambda x: {
        "fillColor": colormap(x["properties"][metrica])
        if x["properties"][metrica] is not None
        else "transparent",
        "color": "black",
        "fillOpacity": 0.4,
    },
    tooltip=tooltip,
).add_to(m)

colormap.add_to(m)

for nome in list(muns_prox_dict.keys()):    
    folium.Marker(
        location=[
            centroids[centroids['NOME']==nome].centroid.values[0].y, 
            centroids[centroids['NOME']==nome].centroid.values[0].x
        ],
        icon = folium.Icon(color = 'red' if nome == mun else 'blue')
    ).add_to(m)

m

In [75]:
bar_plot(
    df = comp_df('TEMP_MED', mun_df, all_muns, muns_prox_names).sort_values(by='NOME'), 
    x = 'TEMP_MED', 
    y = 'NOME', 
    title = 'Temperatura média anual', 
    leg_x = 'Temperatura média anual (C)',
    leg_y = None ,
    text = 'TEMP_MED'
)

In [77]:
bar_plot(
    df = comp_df('PREC_MED', mun_df, all_muns, muns_prox_names).sort_values(by='NOME'), 
    x = 'PREC_MED', 
    y = 'NOME', 
    title = 'Precipitação média anual', 
    leg_x = 'Precipitação média anual (mm)',
    leg_y = None ,
    text = 'PREC_MED'
)

In [78]:
bar_plot(
    df = comp_df('QUAL_MED_AGUA', mun_df, all_muns, muns_prox_names).sort_values(by='NOME'),  
    x = 'QUAL_MED_AGUA', 
    y = 'NOME', 
    title = 'Índice de qualidade média da água', 
    leg_x = 'Índice de qualidade média da água',
    leg_y = None ,
    text = 'QUAL_MED_AGUA'
)

In [79]:
bar_plot(
    df = comp_df('AREA_IRRIGADA_TOT', mun_df, all_muns, muns_prox_names).sort_values(by='NOME'),  
    x = 'AREA_IRRIGADA_TOT', 
    y = 'NOME', 
    title = 'Área irrigada', 
    leg_x = 'Área irrigada (ha)',
    leg_y = None ,
    text = 'AREA_IRRIGADA_TOT'
)

In [80]:
bar_plot(
    df = comp_df('AREA_IRRIGADA_POT_E', mun_df, all_muns, muns_prox_names).sort_values(by='NOME'),  
    x = 'AREA_IRRIGADA_POT_E', 
    y = 'NOME', 
    title = 'Área adicional irrigada potencial efetiva', 
    leg_x = 'AAI potencial efetiva (ha)',
    leg_y = None ,
    text = 'AREA_IRRIGADA_POT_E'
)

In [81]:
bar_plot(
    df = comp_df('DIST_CORPO_AGUA', mun_df, all_muns, muns_prox_names).sort_values(by='NOME'),  
    x = 'DIST_CORPO_AGUA', 
    y = 'NOME', 
    title = "Distância para o corpo d'água mais próximo", 
    leg_x = "Dist. para o corpo d'água mais próximo (Km)",
    leg_y = None ,
    text = 'DIST_CORPO_AGUA'
)

In [85]:
agro_mun, agro_prox = agro_comp(agro, 'VALOR_PROD',muns_prox_names)
fig = make_subplots(rows=1, cols=2, subplot_titles=('Município potencial', 'Total do entorno'))
trace1 = px.bar(
    agro_mun,
    x='VALOR_PROD',
        y='PRODUTO',
    orientation='h'
)
fig.add_trace(trace1.data[0], row=1, col=1)

trace2 = px.bar(
    agro_prox,
     x='VALOR_PROD',
    y='PRODUTO',
    orientation='h',
)
fig.add_trace(trace2.data[0], row=1, col=2)

fig.update_layout(
    title='Produtos agrícolas mais comercializados',
    yaxis=dict(title='Produtos'),
    xaxis=dict(title='Valor comercializado (R$)')
)

In [86]:
agro_mun, agro_prox = agro_comp(agro, 'AREA_PLANTADA',muns_prox_names)
fig = make_subplots(rows=1, cols=2, subplot_titles=('Município potencial', 'Total do entorno'))
trace1 = px.bar(
    agro_mun,
    x='AREA_PLANTADA',
        y='PRODUTO',
    orientation='h'
)
fig.add_trace(trace1.data[0], row=1, col=1)

trace2 = px.bar(
    agro_prox,
     x='AREA_PLANTADA',
    y='PRODUTO',
    orientation='h',
)
fig.add_trace(trace2.data[0], row=1, col=2)

fig.update_layout(
    title='Produtos agrícolas com maior área plantada',
    yaxis=dict(title='Produtos'),
    xaxis=dict(title='Área plantada (ha)')
)

In [89]:
agro_mun, agro_prox = agro_comp(agro, 'REND_AREA', muns_prox_names)
fig = make_subplots(rows=1, cols=2, subplot_titles=('Município potencial', 'Média do entorno'))
trace1 = px.bar(
    agro_mun,
    x='REND_AREA',
    y='PRODUTO',
    orientation='h'
)
fig.add_trace(trace1.data[0], row=1, col=1)

trace2 = px.bar(
    agro_prox,
    x='REND_AREA',
    y='PRODUTO',
    orientation='h',
)
fig.add_trace(trace2.data[0], row=1, col=2)

fig.update_layout(
    title='Produtos agrícolas com maior valor comercializado por área plantada',
    yaxis=dict(title='Produtos'),
    xaxis=dict(title='Valor comercializado (R$)/Área plantada (ha)')
)

In [91]:
solos_mun = solos[['SOLO', 'AREA_TOTAL']].loc[solos['NOME']==mun].sort_values(by='AREA_TOTAL')
solos_prox = solos[solos['NOME'].isin(muns_prox_names)]
solos_prox = solos_prox[['SOLO', 'AREA_TOTAL']].groupby('SOLO').sum().reset_index().sort_values(by='AREA_TOTAL')

fig = make_subplots(
    rows=1, 
    cols=2, 
    subplot_titles=('Município potencial', 'Total do entorno'),
    horizontal_spacing = 0.3
    )
trace1 = px.bar(
    solos_mun,
    x='AREA_TOTAL',
    y='SOLO',
    orientation='h'
)
fig.add_trace(trace1.data[0], row=1, col=1)

trace2 = px.bar(
    solos_prox,
    x='AREA_TOTAL',
    y='SOLO',
    orientation='h'
)
fig.add_trace(trace2.data[0], row=1, col=2)

fig.update_layout(
    title='Tipos de solos mais comuns',
    yaxis=dict(title='Solos'),
    xaxis=dict(title='Área total (ha)')
)

fig.show() 

In [93]:
all_muns.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
Int64Index: 1258 entries, 0 to 1257
Data columns (total 66 columns):
 #   Column                   Non-Null Count  Dtype   
---  ------                   --------------  -----   
 0   IBGE7                    1258 non-null   int64   
 1   UF                       1258 non-null   object  
 2   NOME                     1258 non-null   object  
 3   LATITUDE                 1258 non-null   float64 
 4   LONGITUDE                1258 non-null   float64 
 5   DIST_EF_PUB              1258 non-null   float64 
 6   DIST_EM_PUB              1258 non-null   float64 
 7   IDEB_AI                  1258 non-null   float64 
 8   IDEB_AF                  1258 non-null   float64 
 9   DOCSUP_EF_PUB            1258 non-null   float64 
 10  DOCSUP_EM_PUB            1258 non-null   float64 
 11  TXNASC7C                 1258 non-null   float64 
 12  TXNBAIXOP                1258 non-null   float64 
 13  PINTERSAP                1258 non-null   float64 
 14  